In [147]:
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from nltk.tokenize import word_tokenize
from bs4 import BeautifulSoup
import pandas as pd
import spacy
from spacy.pipeline import EntityRuler
from spacy.lang.en import English
from spacy.tokens import Doc

#gensim
import gensim
from gensim import corpora
import requests
from sklearn.feature_extraction.text import CountVectorizer

#Visualization
from spacy import displacy
from wordcloud import WordCloud
import plotly.express as px
import matplotlib.pyplot as plt

#Data loading/ Data manipulation
import pandas as pd
import numpy as np

#nltk
import re
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
nltk.download(['stopwords','wordnet'])
from sklearn.metrics.pairwise import cosine_similarity

#warning
import warnings 
warnings.filterwarnings('ignore')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\bhupa\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\bhupa\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [6]:
df=pd.read_csv('Resume.csv')

In [14]:
folder_path = r'C:\Users\bhupa\Downloads\archive\data\data'
pdf_files = []

# Recursively find all PDF files in the specified folder and its subfolders
for root, dirs, files in os.walk(folder_path):
    for file in files:
        if file.endswith('.pdf'):
            pdf_files.append(os.path.join(root, file))

In [64]:
def extract_text_from_pdf(pdf_path):
    text = ""
    with open(pdf_path, 'rb') as pdf_file:
        pdf_reader = PyPDF2.PdfReader(pdf_file)
        for page_num in range(len(pdf_reader.pages)):
            page = pdf_reader.pages[page_num]
            text += page.extract_text()
    return text

# Create a dictionary to store the extracted details
details = {}

for pdf_path in pdf_files:
    pdf_text = extract_text_from_pdf(pdf_path)
    pdf_text = pdf_text.lower()
    pdf_text = re.sub('[^a-z]', ' ', pdf_text)
    details[pdf_path] = pdf_text

In [65]:
for pdf_path, pdf_text in details.items():
        pdf_text=pdf_text.replace("\n","")


In [101]:
import requests

# Define the URL with the parameters
url = "https://datasets-server.huggingface.co/rows"
params = {
    "dataset": "jacob-hugging-face/job-descriptions",
    "config": "default",
    "split": "train",
    "offset": 0,
    "limit": 100
}

# Send a GET request
response = requests.get(url, params=params)

# Check if the request was successful
if response.status_code == 200:
    # Get the content of the response and split it into lines
    rows = response.text.split('\n')
    
    # Now 'rows' contains a list of rows as plain text lines, and you can work with it as needed
    print(rows)
else:
    print(f"Request failed with status code {response.status_code}: {response.text}")

['{"features":[{"feature_idx":0,"name":"company_name","type":{"dtype":"string","_type":"Value"}},{"feature_idx":1,"name":"job_description","type":{"dtype":"string","_type":"Value"}},{"feature_idx":2,"name":"position_title","type":{"dtype":"string","_type":"Value"}},{"feature_idx":3,"name":"description_length","type":{"dtype":"int64","_type":"Value"}},{"feature_idx":4,"name":"model_response","type":{"dtype":"string","_type":"Value"}}],"rows":[{"row_idx":0,"row":{"company_name":"Google","job_description":"minimum qualifications\\nbachelors degree or equivalent practical experience years of experience in saas or productivity tools businessexperience managing enterprise accounts with sales cycles\\npreferred qualifications\\n years of experience building strategic business partnerships with enterprise customersability to work through and with a reseller ecosystem to scale the businessability to plan pitch and execute a territory business strategyability to build relationships and to delive

In [110]:
rows = [row.lower() for row in rows]
new_rows = []
for row in rows:
    cleaned_row = re.sub('[^a-zA-Z0-9]', ' ', row)
    new_rows.append(cleaned_row)

In [114]:
def listToString(s):
 
    # initialize an empty string
    str1 = ""
 
    # traverse in the string
    for ele in s:
        str1 += ele
 
    # return string
    return str1
new_rows=listToString(new_rows)

In [116]:
descriptions = re.findall(r'job description(.*?)position title', new_rows, re.DOTALL | re.IGNORECASE)

# Clean up descriptions (remove leading/trailing whitespace)
clean_descriptions = [desc.strip() for desc in descriptions]

# Print the descriptions
for i, description in enumerate(clean_descriptions, 1):
    print(f"Company {i} Description:")
    print(description)
    print("\n" + "=" * 50 + "\n")

Company 1 Description:
type    dtype   string    type   value      feature idx  2  name


Company 2 Description:
minimum qualifications nbachelors degree or equivalent practical experience years of experience in saas or productivity tools businessexperience managing enterprise accounts with sales cycles npreferred qualifications n years of experience building strategic business partnerships with enterprise customersability to work through and with a reseller ecosystem to scale the businessability to plan pitch and execute a territory business strategyability to build relationships and to deliver results in a crossfunctionalmatrixed environmentability to identify crosspromoting and uppromoting opportunities within the existing account baseexcellent account management writtenverbal communication strategic and analyticalthinking skills nabout the job nas a member of the google cloud team you inspire leading companies schools and government agencies to work smarter with google tools like g

In [120]:
all_descriptions = ""
for i, description in enumerate(clean_descriptions, 1):
    all_descriptions += f"Company {i} Description:\n{description}\n\n" + "=" * 50 + "\n"


Company 1 Description:
type    dtype   string    type   value      feature idx  2  name

Company 2 Description:
minimum qualifications nbachelors degree or equivalent practical experience years of experience in saas or productivity tools businessexperience managing enterprise accounts with sales cycles npreferred qualifications n years of experience building strategic business partnerships with enterprise customersability to work through and with a reseller ecosystem to scale the businessability to plan pitch and execute a territory business strategyability to build relationships and to deliver results in a crossfunctionalmatrixed environmentability to identify crosspromoting and uppromoting opportunities within the existing account baseexcellent account management writtenverbal communication strategic and analyticalthinking skills nabout the job nas a member of the google cloud team you inspire leading companies schools and government agencies to work smarter with google tools like go

In [122]:
def extract_company_descriptions(text):
    # Use regular expressions to find company descriptions
    descriptions = re.split(r'={50,}', text)
    
    # Remove any leading/trailing whitespace from each description
    descriptions = [desc.strip() for desc in descriptions if desc.strip()]
    
    return descriptions

# Example text containing company descriptions
text = all_descriptions

# Extract company descriptions and store them in a list
company_descriptions = extract_company_descriptions(text)

# Print the list of descriptions
for i, description in enumerate(company_descriptions, start=1):
    print(f"Company {i} Description:\n{description}\n")

Company 1 Description:
Company 1 Description:
type    dtype   string    type   value      feature idx  2  name

Company 2 Description:
Company 2 Description:
minimum qualifications nbachelors degree or equivalent practical experience years of experience in saas or productivity tools businessexperience managing enterprise accounts with sales cycles npreferred qualifications n years of experience building strategic business partnerships with enterprise customersability to work through and with a reseller ecosystem to scale the businessability to plan pitch and execute a territory business strategyability to build relationships and to deliver results in a crossfunctionalmatrixed environmentability to identify crosspromoting and uppromoting opportunities within the existing account baseexcellent account management writtenverbal communication strategic and analyticalthinking skills nabout the job nas a member of the google cloud team you inspire leading companies schools and government agen

In [136]:
details

{'C:\\Users\\bhupa\\Downloads\\archive\\data\\data\\ACCOUNTANT\\10554236.pdf': 'accountant summary financial accountant specializing in financial planning  reporting and analysis within the department of defense  highlights account reconciliations results oriented financial reporting critical thinking accounting operations professional analysis of financial systems erp  enterprise resource planning  software  excellent facilitator accomplishments served on a tiger team which identified and resolved general ledger postings in deams totaling     b in accounting adjustments  this allowed for the first successful fiscal year end close for       in collaboration with dfas europe  developed an automated tool that identified duplicate obligations  this tool allowed hq usafe to deobligate over   m in duplicate obligations  experience company name   july        to  november        accountant   city      state enterprise resource planning office  ero  in this position as an accountant assigned t

In [138]:
company_descriptions[7]

'Company 8 Description:\nabout the position n nthe web designer is responsible for providing designrelated support for clientrelated and internal projects n nadditionally the web designer is responsible for providing designrelated support for projects that are currently in development client review and postlaunch when assigned n ndaytoday n collaborate closely with design managers on websiterelated projects including finishing projects that have a set art direction to hand over to the development team n work crossfunctionally with content and development teams which includes facilitating design discussions and adjusting existing designswebsites based on client feedback in preparation for the launch of their sites n partner with development teams to ensure the implementation of your designs and user experiences are of the highest quality n use and evolve our design systemlibrary to craft sketches flows prototypes and highfidelity visuals for client websites and product features n work c

In [139]:
def create_resume_job_pairs(resume_dict, job_descriptions):
    pairs_list = []
    
    for resume_path, resume_content in resume_dict.items():
        for job_description in job_descriptions:
            pairs_list.append((resume_content, job_description))
    cv=CountVectorizer()
    count_matrix=cv.fit_transform(pairs_list)
    return cosine_similarity(count_matrix))
    #return pairs_list

In [155]:
# Create pairs
create_resume_job_pairs(details, newcom)

# The 'pairs' list will contain pairs of resumes and job descriptions
for pair in pairs:
    resume, job_description = pair
#     print("Resume:", resume)
#     print("Job Description:", job_description)
#     print()


In [154]:
newcom=company_descriptions[:5]

In [156]:
def create_resume_job_pairs(resume_dict, job_descriptions):
    pairs_list = []
    
    for resume_content in resume_dict.values():
        for job_description in job_descriptions:
            pairs_list.append(resume_content + ' ' + job_description)  # Combine resume and job description
    
    cv = CountVectorizer()
    count_matrix = cv.fit_transform(pairs_list)
    
    cosine_sim = cosine_similarity(count_matrix, count_matrix)
    
    return cosine_sim

In [158]:
cosine_similarity_matrix = create_resume_job_pairs(details, newcom)

# Print the cosine similarity matrix
print(cosine_similarity_matrix)

[[1.         0.99669989 0.99910889 ... 0.70378112 0.76587369 0.75605661]
 [0.99669989 1.         0.99694424 ... 0.71779702 0.78046093 0.77024075]
 [0.99910889 0.99694424 1.         ... 0.71736308 0.77447328 0.764713  ]
 ...
 [0.70378112 0.71779702 0.71736308 ... 1.         0.96008967 0.96180516]
 [0.76587369 0.78046093 0.77447328 ... 0.96008967 1.         0.95280476]
 [0.75605661 0.77024075 0.764713   ... 0.96180516 0.95280476 1.        ]]


In [161]:
def rank_cvs_by_similarity(cosine_sim, cv_names, job_desc_names):
    ranked_cvs = {}
    
    for i, job_desc in enumerate(job_desc_names):
        similarities = cosine_sim[i]
        cv_indices_sorted = np.argsort(similarities)[::-1]  # Sort indices in descending order
        
        top_cvs = []
        for j in cv_indices_sorted[:5]:  # Get the top 5 CVs
            top_cvs.append(cv_names[j])
        
        ranked_cvs[job_desc] = top_cvs
    
    return ranked_cvs



cv_names = list(details.keys())


ranked_cvs = rank_cvs_by_similarity(cosine_similarity_matrix, cv_names, newcom)

# Print the top 5 CVs for each job description
for job_desc, top_cvs in ranked_cvs.items():
    print(f"Top 5 CVs for '{job_desc}':")
    for cv in top_cvs:
        print(cv)
    print()


Top 5 CVs for 'Company 1 Description:
type    dtype   string    type   value      feature idx  2  name':
C:\Users\bhupa\Downloads\archive\data\data\ACCOUNTANT\10554236.pdf
C:\Users\bhupa\Downloads\archive\data\data\ACCOUNTANT\11163645.pdf
C:\Users\bhupa\Downloads\archive\data\data\ACCOUNTANT\12065211.pdf
C:\Users\bhupa\Downloads\archive\data\data\ACCOUNTANT\10674770.pdf
C:\Users\bhupa\Downloads\archive\data\data\ACCOUNTANT\11759079.pdf

Top 5 CVs for 'Company 2 Description:
minimum qualifications nbachelors degree or equivalent practical experience years of experience in saas or productivity tools businessexperience managing enterprise accounts with sales cycles npreferred qualifications n years of experience building strategic business partnerships with enterprise customersability to work through and with a reseller ecosystem to scale the businessability to plan pitch and execute a territory business strategyability to build relationships and to deliver results in a crossfunctionalmat